## Installation des librairies nécessaires

In [ ]:
!pip install confluent-kafka

# LogAnalyser Producer
Nous sommes enfin prêts à envoyer des données à Apache Kafka à l'aide des clients Python Confluent_Kafka.Producer et AdminClient pour generer le topic necesssaire

In [3]:
import pandas as pd
import numpy as np
from datetime import datetime


### Télécharger le fichier access.log.2

In [1]:
!curl "https://network-data-traffic.s3.amazonaws.com/access.log.2" > access.log.2

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0 37.7M    0  339k    0     0   178k      0  0:03:37  0:00:01  0:03:36  178k
 11 37.7M   11 4520k    0     0  1575k      0  0:00:24  0:00:02  0:00:22 1575k
 26 37.7M   26  9.9M    0     0  2628k      0  0:00:14  0:00:03  0:00:11 2627k
 41 37.7M   41 15.8M    0     0  3327k      0  0:00:11  0:00:04  0:00:07 3327k
 57 37.7M   57 21.8M    0     0  3816k      0  0:00:10  0:00:05  0:00:05 4520k
 70 37.7M   70 26.6M    0     0  3979k      0  0:00:09  0:00:06  0:00:03 5438k
 84 37.7M   84 31.8M    0     0  4146k      0  0:00:09  0:00:07  0:00:02 5621k
 95 37.7M   95 36.1M    0     0  4174k      0  0:00:09  0:00:08  0:00:01 5370k
100 37.7M  100 37.7M    0     0  4238k      0  0:00

### Créer un topic logAnalyser

In [19]:
from confluent_kafka.admin import AdminClient, NewTopic

a = AdminClient({'bootstrap.servers': '51.79.25.30:29092','debug': 'broker,admin'})

new_topics = [NewTopic('log-analyzis', num_partitions=3, replication_factor=1)
# Note : Dans un scénario de production multi-clusters, il est plus habituel d'utiliser un facteur de réplication de 3 pour la durabilité.

# Appelez create_topics pour créer des sujets de manière asynchrone. Un dict # de <topic,future> est renvoyé
fs = a.create_topics(new_topics)

# Attendre la fin de chaque opération.
for topic, f in fs.items():
    try:
        f.result()  # Le résultat en lui-même est None
        print("Topic {} created".format(topic))
    except Exception as e:
        print(e)
        print("Failed to create topic {}: {}".format(topic, e))


SyntaxError: invalid syntax (<ipython-input-19-1662cb2c029d>, line 9)

## 2 Créer des Kafka Procuders
### Initialisation
Le producteur est configuré à l'aide d'un dictionnaire comme suit:

In [20]:
from confluent_kafka import Producer
import socket
import json
conf = {'bootstrap.servers': "PLAINTEXT://51.79.25.30:29092,PLAINTEXT://51.79.25.30:9092",
        'client.id': socket.gethostname(), 'queue.buffering.max.messages': 1000000,
                'queue.buffering.max.ms': 5000,
                'batch.num.messages': 100,
                'log.connection.close': False,
                'client.id': socket.gethostname(),
                'default.topic.config': {'acks': 'all'}}

 

### 2 -Ingester les données en utilsant un topic log-analyser, key =idligne et value =ligne.
       

In [22]:
#Initialiser producer avec la configuration 
p = Producer(conf)
# initialiser le nom du topic
topic_name='log-analyzis'

def delivery_report(err, msg):
    """ Called once for each message produced to indicate delivery result.
        Triggered by poll() or flush(). """
    if err is not None:
        print('Message delivery failed: {}'.format(err))
    else:
        print('Message delivered to {} [{}]'.format(msg.topic(), msg.partition()))
 
# Parcourir comme key-value et generer un ecrire les données (keyn value) avec p.produce
### Lire le fichier access.log2 file
i=0
with open('access.log.2') as f:
    txt = f.readlines()
    for line in txt:
        
        # Lancer un rappel de rapport de livraison disponible à partir d'appels de production () précédents
        p.poll(0)
        i=i+1
        # Produire de manière synchrone un message, les callbacks
        # seront déclenchés à partir de poll() au-dessus, ou de flush() au-dessous, lorsque le message a
        # ont été livrés avec succès ou ont échoué définitivement.
        data = json.dumps(line, ensure_ascii=False).encode('utf-8')

        p.produce(topic_name,value=data, key=str(i), callback=delivery_report)
     
    
# Attendre la remise des messages en attente et du rapport de remise
# les callbacks à déclencher.
p.flush()

Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message delivered to log-analyzis [0]
Message deli

0